In [1]:
from typing import List

import requests

from google import genai
from google.genai import types

from pydantic import BaseModel, Field

In [2]:
class Article(BaseModel):
    title: str
    authors: List[str]
    topics: List[str]
    short: str = Field(description='Short summary, max 25 words')

In [3]:
URL = 'https://download.tvaroska.sk'
ARTICLE = 'https://garymarcus.substack.com/p/peak-bubble'

In [4]:
md = requests.Session()
md.headers.update({'X-API-Key':'value', 'Accept': 'text/markdown'})

pdf = requests.Session()
pdf.headers.update({'X-API-Key':'value', 'Accept': 'application/pdf'})

In [5]:
client = genai.Client(
    vertexai=True, 
    location='us-central1',
    http_options=types.HttpOptions(
       api_version="v1",
       headers={
           "X-Vertex-AI-LLM-Request-Type": "flex"
       },
       timeout = 1000000
   )
)

In [6]:
markdown = md.get(f'{URL}/{ARTICLE}').content.decode()

In [7]:
response = client.models.generate_content(
    model = 'gemini-2.5-flash',
    contents=[
        f"Summarize the article: {markdown}"],
    config=types.GenerateContentConfig(
        response_mime_type='application/json',
        response_schema=Article,
    ),

)

In [8]:
Article.model_validate_json(response.candidates[0].content.parts[0].text)

Article(title='Peak bubble', authors=['Gary Marcus'], topics=['GenAI bubble', 'AI valuations', 'Oracle', 'OpenAI', 'tech market', 'market bubble'], short="The author argues the GenAI and tech markets are in an unsustainable bubble, citing questionable deals and inflated valuations like Oracle's recent surge.")

In [9]:
content = pdf.get(f'{URL}/{ARTICLE}')

In [10]:
parts = ['Summarize the article', types.Part.from_bytes(
    data = content.content,
    mime_type='application/pdf'
)]

In [11]:
response = client.models.generate_content(
    model = 'gemini-2.5-flash',
    contents=parts,
    config=types.GenerateContentConfig(
        response_mime_type='application/json',
        response_schema=Article,
    ),

)

In [12]:
Article.model_validate_json(response.candidates[0].content.parts[0].text)

Article(title='Peak bubble', authors=['GARY MARCUS'], topics=['AI', 'Business', 'Economics', 'Speculative Bubbles'], short='Gary Marcus critiques the Oracle-OpenAI deal, likening it to Tulip Mania, as a sign of an unsustainable AI speculative bubble.')

In [13]:
with open('a.pdf', 'wb+') as f:
    f.write(content.content)

In [15]:
content.content

b'%PDF-1.4\n%\xd3\xeb\xe9\xe1\n1 0 obj\n<</Title (Peak bubble - by Gary Marcus - Marcus on AI)\n/Creator (Mozilla/5.0 \\(X11; Linux x86_64\\) AppleWebKit/537.36 \\(KHTML, like Gecko\\) HeadlessChrome/140.0.0.0 Safari/537.36)\n/Producer (Skia/PDF m140)\n/CreationDate (D:20250913230637+00\'00\')\n/ModDate (D:20250913230637+00\'00\')>>\nendobj\n3 0 obj\n<</ca 1\n/BM /Normal>>\nendobj\n6 0 obj\n<</CA 1\n/ca 1\n/LC 0\n/LJ 0\n/LW 1\n/ML 4\n/SA true\n/BM /Normal>>\nendobj\n7 0 obj\n<</CA 1\n/ca 1\n/LC 1\n/LJ 1\n/LW 2\n/ML 4\n/SA true\n/BM /Normal>>\nendobj\n10 0 obj\n<</N 3\n/Filter /FlateDecode\n/Length 293>> stream\nx\x9c}\x90\xbdJ\xc3\x00\x14\x85\xbf\xd4\x82(\x8a\x83\x0e\x1d\x1c28\xb8h\x93\xa6iRpi"\x16\xd7V\xa1\xa9S\x92\xa6A\xecOHS\xf4\x01tspu+.\xbe\x80\xe8c(\x08\x0e\xe2\xe0#\x88\xa0\xb3\xa4AR\x90x\xe0\xc2\xc7\xe1\xc0\xbd\xf7@\xae\x00\x90\x97\xa0?\x88\xc2F\xdd\x10[V[\x9c\x7fG@`*\xdb\x1d\x05dK\x80\xef\x97$\xfb\xbc\xf5O.K\x0b\x1do\xe4\x02\x1f@\x14\xb6\xac6\x08\x1d`\xcdO\xf8,f\'\xe1\xcb\x98O\